In [1]:
import os
import json
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import random
from tqdm import tqdm
import seaborn as sns
import pickle
import json

In [2]:
combined_df = pd.read_csv('./../data/combined_data.csv')

C:\Users\jhama\AppData\Local\Temp\ipykernel_17484\4217704378.py:1: DtypeWarning: Columns (1,2,3,4,6,8,9,15,16,21,22,23,25,27,30,31,32,34,35,36,43,44,46,48,50,52,61,67,68,74,75,79,84,85,86,87,91,92,95,96,97,100,101,103,104,106,107,114,115,117,119,120,121,122,123,125,127,128,129,130,132,133,144,145,152,165,166,167,168,169,170,171,172,173,174,175,177,178,179,181,183,184,185,186,187,188,189,190,191,192,193,194,195,196,197,198,199,200,201,202,203,205,206,207,209,210,211,212,215,216,217,218,219,220,222,223,224,225,226,227,228,230,232,233,234) have mixed types. Specify dtype option on import or set low_memory=False.
  combined_df = pd.read_csv('./../data/combined_data.csv')


In [3]:
final_df = pd.read_csv('./../data/final_data.csv')

C:\Users\jhama\AppData\Local\Temp\ipykernel_17484\2618174272.py:1: DtypeWarning: Columns (0,4,21,22) have mixed types. Specify dtype option on import or set low_memory=False.
  final_df = pd.read_csv('./../data/final_data.csv')


In [4]:
print(combined_df.shape)
print(final_df.shape)

(104944, 317)
(104944, 23)


In [5]:
final_df['title'] = combined_df['title']
final_df['asin'] = combined_df['asin']

In [6]:
final_df.to_csv('./../data/cleaned/final_modified.csv')

In [7]:
rel2id_dict = {col: idx for idx, col in enumerate(final_df.columns)}
#rel2id_dict

In [8]:
unique_entities = pd.unique(final_df.values.ravel('K'))
ent2id_dict = {entity: idx for idx, entity in enumerate(unique_entities) if pd.notnull(entity)}
len(ent2id_dict)

264852

In [9]:
# Save rel2id_dict as a .pkl file
with open('./../data/cleaned/rel2id_dict.pkl', 'wb') as f:
    pickle.dump(rel2id_dict, f)

# Save ent2id_dict as a .pkl file
with open('./../data/cleaned/ent2id_dict.pkl', 'wb') as f:
    pickle.dump(ent2id_dict, f)

In [10]:
# Save rel2id_dict as a .txt file with utf-8 encoding
with open('./../data/cleaned/rel2id_dict.txt', 'w', encoding='utf-8') as f:
    for key, value in rel2id_dict.items():
        f.write(f"{key}:{value}\n")

# Save ent2id_dict as a .txt file with utf-8 encoding
with open('./../data/cleaned/ent2id_dict.txt', 'w', encoding='utf-8') as f:
    for key, value in ent2id_dict.items():
        f.write(f"{key}:{value}\n")

In [11]:
final_df.head()

voltage_unit material_type_free  material age_range_description light_type  \
0          NaN           BPA Free       NaN                  Baby        NaN   
1          NaN                NaN       NaN                   Kid        NaN   
2          NaN    Phthalates Free       NaN                   NaN        NaN   
3          NaN           BPA Free       NaN                   Kid        NaN   
4          NaN           BPA Free  BPA Free                  Baby        NaN   

  product_type                 color shelf_life_unit flavor        binding  \
0  BABY_BOTTLE  Orange, Yellow, Gray             NaN    NaN  miscellaneous   
1  BABY_BOTTLE                 Multi             NaN    NaN   baby_product   
2  BABY_BOTTLE                 Black             NaN    NaN   baby_product   
3  BABY_BOTTLE            multicolor             NaN    NaN         sports   
4  BABY_BOTTLE                   NaN             NaN    NaN   baby_product   

   ...           brand container_type item_height_bin item_length_bin  \
0  ...           Copco            NaN             NaN             NaN   
1  ...            Nuby            NaN             NaN             NaN   
2  ...  J.L. Childress            NaN   BABY_BOTTLE_1   BABY_BOTTLE_1   
3  ...    Baby Fanatic            NaN   BABY_BOTTLE_1   BABY_BOTTLE_1   
4  ...     Dr. Brown's            NaN   BABY_BOTTLE_1   BABY_BOTTLE_1   

  item_volume_value_bin item_width_bin battery_capacity_value_bin  \
0                   NaN            NaN                        NaN   
1                   NaN            NaN                        NaN   
2                   NaN  BABY_BOTTLE_1                        NaN   
3                   NaN  BABY_BOTTLE_1                        NaN   
4                   NaN  BABY_BOTTLE_1                        NaN   

  battery_weight_value_bin                                              title  \
0                      NaN  Copco Hydra Reusable Tritan Water Bottle Spill...   
1                      NaN  Nuby Thirsty Kids Push Button Flip-it Soft Spo...   
2                      NaN  J.L. Childress MaxiCOOL 4 Bottle Breastmilk Co...   
3                      NaN  Baby Fanatic NCAA Alabama Crimson Tide Unisex ...   
4                      NaN          Dr. Brown's Pink 8 Ounce Bottles (2 Pack)   

         asin  
0  B07MZCMZNG  
1  B07T175PWC  
2  B0009RNXNK  
3  B06XXTX2H2  
4  B00JLVEJ88  

[5 rows x 25 columns]

In [12]:
df = final_df

In [13]:
df.shape

(104944, 25)

In [14]:
df.columns

Index(['voltage_unit', 'material_type_free', 'material',
       'age_range_description', 'light_type', 'product_type', 'color',
       'shelf_life_unit', 'flavor', 'binding', 'scent',
       'battery_cell_composition', 'bullet_point', 'item_volume_unit',
       'manufacturer', 'brand', 'container_type', 'item_height_bin',
       'item_length_bin', 'item_volume_value_bin', 'item_width_bin',
       'battery_capacity_value_bin', 'battery_weight_value_bin', 'title',
       'asin'],
      dtype='object')

In [15]:
# Generate and write triples to a .txt file
with open('./../data/cleaned/triples.txt', 'w', encoding='utf-8') as f:
    for index, row in df.iterrows():
        asin_id = ent2id_dict[row['asin']]
        for col in df.columns:
            if col != 'asin':  # Skip the 'asin' column
                relation_id = rel2id_dict[col]
                value = row[col]
                if pd.notnull(value):  # Skip NaN values
                    value_id = ent2id_dict[value]
                    f.write(f"{asin_id} {relation_id} {value_id}\n")

In [16]:
context_filter_dict = {}

In [17]:
# Load the JSON file into a dictionary
with open('category_attribute_frequency.json', 'r', encoding='utf-8') as f:
    category_attribute_frequency_dict = json.load(f)

# Optional: Print a sample of the dictionary
print(type(category_attribute_frequency_dict))  # Should print: <class 'dict'>
print(list(category_attribute_frequency_dict.keys())[:5])

<class 'dict'>
['BABY_BOTTLE', 'BAKING_MIX', 'BATHWATER_ADDITIVE', 'BATTERY', 'BLOOD_PRESSURE_MONITOR']


In [18]:
print(len(list(category_attribute_frequency_dict.keys())))

12


In [19]:
for prod_key, prod_value in category_attribute_frequency_dict.items():
    context_filter_dict[prod_key] = {}
    for attr_key, attr_value in prod_value.items():
        context_filter_dict[prod_key][attr_key] = {'context': None, 'filter': None}
        
        # Sort and handle the attribute values
        sorted_attr = dict(sorted(attr_value.items(), key=lambda item: item[1], reverse=True))
        
        # Remove empty string keys
        if '' in sorted_attr:
            del sorted_attr['']
        
        # Convert keys to a list and handle slicing
        keys_list = list(sorted_attr.keys())
        
        if len(keys_list) < 10:
            context_filter_dict[prod_key][attr_key]['filter'] = keys_list
        else:
            context_filter_dict[prod_key][attr_key]['filter'] = keys_list[1:10]
            context_filter_dict[prod_key][attr_key]['context'] = keys_list[10:]

In [20]:
for prod_key, prod_value in context_filter_dict.items():
    print(prod_key, len(prod_value[list(prod_value.keys())[0]]['context']))

BABY_BOTTLE 88
BAKING_MIX 25
BATHWATER_ADDITIVE 78
BATTERY 33
BLOOD_PRESSURE_MONITOR 106
BODY_DEODORANT 34
BODY_LUBRICANT 30
BREAD 13
BREAKFAST_CEREAL 18
CAKE 41
CANDLE 254
CANDY 55


In [21]:
context_filter_dict

{'BABY_BOTTLE': {'color': {'context': ['multicolored',
    'multi/none',
    'multicolors',
    'natural/orange',
    'gold white',
    'multi-colored',
    'muliticolored',
    'simply red',
    'blue, yellow',
    'blue, orange',
    'blue dinosaur',
    'multicolour',
    'sky blue/pink',
    'orange swirl',
    'in dribble dots blue',
    'in baby blue stripe',
    'blue - cookiecrumb',
    'teal / green / blue',
    'blue-white',
    'blue sailboat',
    'mist gray',
    'blueberry',
    'blue giraffe',
    'blue elephant',
    'blue/purple/pink',
    'chicago white sox',
    'purple/pink/yellow/red/blue/teal',
    'stainless steel water bottle - white',
    'clear w/ red, yellow, & white lids',
    'white-usb',
    'pink elephant and blue space',
    'green/blue/orange',
    'natural mirror blue',
    'gray gold',
    'green & white',
    'radiant red',
    'off-white-l501',
    'green/blue/teal',
    'red, white',
    'pink and blue',
    'blue/tan/white',
    'blue sea, orange 

In [22]:
with open('./../data/cleaned/context_filter_sep.json', 'w', encoding='utf-8') as f:
    json.dump(context_filter_dict, f, ensure_ascii=False, indent=4)

In [23]:
print(len(context_filter_dict))

12


In [24]:
final_df.head(1)

voltage_unit material_type_free material age_range_description light_type  \
0          NaN           BPA Free      NaN                  Baby        NaN   

  product_type                 color shelf_life_unit flavor        binding  \
0  BABY_BOTTLE  Orange, Yellow, Gray             NaN    NaN  miscellaneous   

   ...  brand container_type item_height_bin item_length_bin  \
0  ...  Copco            NaN             NaN             NaN   

  item_volume_value_bin item_width_bin battery_capacity_value_bin  \
0                   NaN            NaN                        NaN   

  battery_weight_value_bin                                              title  \
0                      NaN  Copco Hydra Reusable Tritan Water Bottle Spill...   

         asin  
0  B07MZCMZNG  

[1 rows x 25 columns]

In [25]:
import pandas as pd

# Initialize lists to store the data
asin_list = []
title_list = []
context_list = []
filter_list = []
bullet_list = []
# Iterate over each row in the DataFrame
for index, row in final_df.iterrows():
    asin_id = row['asin']
    title = row['title']
    product_type = row['product_type']
    
    # Initialize empty lists for context and filter for this row
    context = [product_type]
    filter_ = [] 
    #print(asin_id)
    # Iterate over each column in the row
    for col in final_df.columns:
        
        if col == 'asin' or col == 'title' or col == 'product_type':
            continue
        
        value = row[col]
        if col == 'bullet_point':
            bullet_list.append(f"{col}:{value}")
            continue
       # print(col,value)
        # Skip if value is None or NaN
        if pd.notnull(value):
            # Check in the context_filter_dict if the value should be added to context or filter
            if product_type in context_filter_dict:
                if col in context_filter_dict[product_type]:
                    if context_filter_dict[product_type][col]['filter'] is not None and value.lower() in context_filter_dict[product_type][col]['filter']:
                        filter_.append(f"{col}:{value}")
                    else:
                        context.append(f"{col}:{value}")
   
    # Append to the corresponding lists
    asin_list.append(asin_id)
    title_list.append(title)
    context_list.append(context)
    filter_list.append(filter_)
    
# Create the new DataFrame
template_df = pd.DataFrame({
    'asin_id': asin_list,
    'title': title_list,
    'context': context_list,
    'filter': filter_list,
    'bullet_points' : bullet_list
})

# Display the new DataFrame
print(template_df)


           asin_id                                              title  \
0       B07MZCMZNG  Copco Hydra Reusable Tritan Water Bottle Spill...   
1       B07T175PWC  Nuby Thirsty Kids Push Button Flip-it Soft Spo...   
2       B0009RNXNK  J.L. Childress MaxiCOOL 4 Bottle Breastmilk Co...   
3       B06XXTX2H2  Baby Fanatic NCAA Alabama Crimson Tide Unisex ...   
4       B00JLVEJ88          Dr. Brown's Pink 8 Ounce Bottles (2 Pack)   
...            ...                                                ...   
104939  B08D6Z4CNS  Houston City Cash Candies 💵 | Surprise Valued ...   
104940  B07MBQC3X3  Ferrero Collection - Rondnoir | Rocher | Raffa...   
104941  B00H69SD70           American Almond Kernel Paste - 45 lb Tub   
104942  B06VT4FC49  Gem Gem Ginger Candy Chewy Ginger Chews (Orang...   
104943  B00BMHXAYS  Pecan Caramels 8oz Box by Pioneer Valley (Soft...   

                                                  context  \
0       [BABY_BOTTLE, material_type_free:BPA Free, age...   
1

In [26]:
template_df.to_csv('./../data/cleaned/template_1.csv', index=False)

In [ ]:
#final_df.to_csv('./../data/cleaned/final_df.csv', index=False)